In [2]:
#import librarires
import numpy as np
import pandas as pd
import datetime
import urllib
 
from bokeh.plotting import *
from bokeh.models import HoverTool
from collections import OrderedDict

import requests

import folium

In [3]:
#best practice is to have an app token from Socrata before you can pull large quantities of data
my_app_token = '#######################'

In [4]:
#designate datasets to use
#FY goes from July 1 in year n-1 to June 30 in year n
#e.g. FY 2017 goes from July 1, 2016 to June 30, 2017
datasets = ({'year': 2017, 'url': 'https://data.cityofnewyork.us/resource/qpyv-8eyi.json'},
            {'year': 2016, 'url': 'https://data.cityofnewyork.us/resource/avxe-2nrn.json'},
            {'year': 2015, 'url': 'https://data.cityofnewyork.us/resource/aagd-wyjz.json'},
            {'year': 2014, 'url': 'https://data.cityofnewyork.us/resource/j7ig-zgkq.json'}
           )

In [5]:
#create datasets to work with

def new_df(datasets, app_token, select_clauses, groupby_clauses, number_of_results):
    '''function to create df we will be working with
    Note: this is slow (like 5-10 minutes slow), as it's reading through ~10M records/year, ~30 records total
    '''
    #list of one year datasets
    annual_dfs = []
    #fill list of one year datasets
    for dataset in datasets:
        attempts = 1
        while attempts <= 5:
            try:
                year_df = read_in(dataset['url'], my_app_token, my_select_clauses, my_groupby_clauses, my_number_of_results)
                annual_dfs.append(year_df)
                print(str(dataset['year']) + ' read in successfully on attempt ' + str(attempts))
                break
            except:
                print(str(dataset['year']) + ' read in attempt ' + str(attempts) + ' failed')
                attempts = attempts + 1
                continue
    #concatenate all the dfs in annual_dfs into one df
    many_year_df = pd.concat(annual_dfs)
    return many_year_df
    
#read in
def read_in (url, app_token, select_clauses, groupby_clauses, number_of_results):
    '''helper function to read in dataset,
    select, group, limit strings are SoQL, Socrata QL like SQL, decides what to pull from json file
    there are a lot more Socrata QL params, all SQL-like that can be added as well
    '''
    one_year_df = pd.read_json(url+
                               "?$$app_token="+app_token+
                               "&$select="+str(select_clauses)+
                               "&$group="+str(groupby_clauses)+
                               "&$limit="+str(number_of_results)
                              )
    return one_year_df

#fill in parameters
my_select_clauses = "count(summons_number),issue_date,violation_county,violation_precinct,violation_code"
my_groupby_clauses = "issue_date,violation_county,violation_precinct,violation_code"
my_number_of_results = 100000000 #arbitrary large number

main_df = new_df(datasets, my_app_token, my_select_clauses, my_groupby_clauses, my_number_of_results)

2017 read in successfully on attempt 1
2016 read in successfully on attempt 1
2015 read in successfully on attempt 1
2014 read in attempt 1 failed
2014 read in attempt 2 failed
2014 read in attempt 3 failed
2014 read in attempt 4 failed
2014 read in attempt 5 failed


In [6]:
#clean up main df
    
def elim_code_36 (dataset):
    '''function to take out all violations with code 36 (other)'''    
    elim_code_36_dataset = dataset[dataset['violation_code']!=36].sort_values('count_summons_number',ascending=False)
    return elim_code_36_dataset

def switch_to_datetime (dataset):
    '''function to change data formats of rows to Y-m-d'''
    dataset['issue_date'] = pd.to_datetime(dataset['issue_date'], format='%Y-%m-%d')
    return dataset

main_df = elim_code_36(main_df)
main_df = switch_to_datetime(main_df)
    
#correct badly coded counties
main_df['violation_county'] = ['NY' if x in set(['MAN','MH','MN','NEW Y','NEWY','NY','NYC'])
                               else 'BX' if x in set(['BRONX','BX'])
                               else 'K' if x in set(['BK','K','KING','KINGS'])
                               else 'Q' if x in set(['Q','QN','QNS','QU','QUEENS'])
                               else 'R' if x in set(['R','RC','RICH','ST'])
                               else 'NA'
                               for x in main_df['violation_county']]

#delete entries that have dates not within normal parameters of data sets
main_df = main_df[(main_df['issue_date'] >= '2013-07-01') & (main_df['issue_date'] < '2016-10-01')]

In [7]:
#add descriptions of violation codes and merge into main_df

#read in violation codes from github
violation_codes = pd.read_csv("https://raw.githubusercontent.com/JBlumstein/NYCParking/master/DOF_Parking_Violation_Codes.csv")

#rename columns on violation_codes df
violation_codes.columns = ['violation_code','definition','manhattan_96_and_below','all_other_areas']

#left join main_df and violation_codes df so that there's more info on violation in main_df
main_df = pd.merge(main_df, violation_codes, on='violation_code', how='left')

#cast precincts as integers from floats (gets messed up by merge)
main_df['violation_precinct'] = main_df['violation_precinct'].astype(int)

In [8]:
#get rid of violations marked from non-existant precincts

#get numbers of precincts from file with map of nyc precincts and put in df
nyc_precincts_geojson = r'http://services5.arcgis.com/GfwWNkhOj9bNBqoJ/arcgis/rest/services/nypp/FeatureServer/0/query?where=1=1&outFields=*&outSR=4326&f=geojson'
file_to_read = requests.get(nyc_precincts_geojson)
j = file_to_read.json()
nyc_precincts = [x['properties']['Precinct'] for x in j['features']]
nyc_precincts_df = pd.DataFrame(nyc_precincts,columns=['violation_precinct'])

#using a join on df of nyc precincts, narrow our df to just real precincts 
main_df = pd.merge(main_df, nyc_precincts_df, on='violation_precinct', how='inner')

In [9]:
#create columns for year, month of year, and day of month of violation

#create column with date as a string 
main_df['issue_date_string'] = main_df['issue_date'].dt.strftime('%Y-%m-%d')

#create column for issue year, cast as int
main_df['issue_year'] = [x[:4] for x in main_df['issue_date_string']]
main_df['issue_year'] = main_df['issue_year'].astype(int)

#create column for issue month of year, cast as int
main_df['issue_month'] = [x[5:7] for x in main_df['issue_date_string']]
main_df['issue_month'] = main_df['issue_month'].astype(int)

#create column for issue day of month, cast as int
main_df['issue_day'] = [x[8:] for x in main_df['issue_date_string']]
main_df['issue_day'] = main_df['issue_day'].astype(int)

In [10]:
#calculate the total summonses in dollars for a violation in a precinct on a day

#create column for portion of precinct 96th st. and below
main_df['portion_manhattan_96_and_below'] = [1.0 if x < 22 or x == 23
                                             else 0.75 if x == 22 \
                                             else 0.5 if x == 24 \
                                             else 0 \
                                             for x in main_df['violation_precinct']]

#create column for average dollar amount of summons based on location
main_df['average_summons_amount'] = (main_df['portion_manhattan_96_and_below'] * main_df['manhattan_96_and_below'] 
                                     + (1 - main_df['portion_manhattan_96_and_below']) * main_df['all_other_areas'])

#get total summons dollars by multiplying average dollar amount by number of summons given
main_df['total_summons_dollars'] = main_df['count_summons_number'] * main_df['average_summons_amount']

In [11]:
#functions to create choropleths with the dataset

#save nyc_precincts_geojson locally - needed for choropleth function to work
nyc_precincts_geojson_saved = r'query.json'

def create_choropleth (dataset, response, violations = set([]), years = set([]), months = set([]), days = set([])):
    '''function to create choropleth graphic'''
    choropleth_dataset = aggregate(dataset, violations, years, months, days)
    NYC_COORDINATES = (40.704294, -73.919277)
    max_value = int(choropleth_dataset[response].max())
    base_threshold_scale = [0, int(max_value/8), int(max_value/4), int(max_value/2), int(3*max_value/4), max_value]
    output_choropleth = folium.Map(location=NYC_COORDINATES, zoom_start=11)
    output_choropleth.choropleth(geo_path=nyc_precincts_geojson_saved, data=choropleth_dataset,
                        columns=['violation_precinct', response], 
                        key_on='feature.properties.Precinct',
                        fill_color='YlGnBu', threshold_scale=base_threshold_scale, line_opacity=0.7,
                        legend_name = 'Number of incidents per district')
    output_choropleth.save('nyc_choropleth.html')
    return output_choropleth

def aggregate(dataset, violations, years, months, days):
    '''helper function that aggregates data into correct dataset for main choropleth function
    e.g. total violations by precinct
    '''
    if violations == set([]):
        violations = set(dataset['violation_code'])
    if years == set([]):
        years = set(dataset['issue_year'])
    if months == set([]):
        months = set(dataset['issue_month'])
    if days == set([]):
        days = set(dataset['issue_day'])
    filtered_dataset = dataset[(dataset['violation_code'].isin(violations)) &
                                  (dataset['issue_year'].isin(years)) &
                                  (dataset['issue_month'].isin(months)) &
                                  (dataset['issue_day'].isin(days))]
    filtered_dataset = filtered_dataset[['violation_precinct','count_summons_number','total_summons_dollars']]
    precinct_offenses_df = filtered_dataset.groupby(['violation_precinct']).aggregate(np.sum).reset_index()
    return precinct_offenses_df

In [12]:
#create a choropleth of summons in dollars for 2015
first_choropleth = create_choropleth(main_df, 'total_summons_dollars', years=[2015])
first_choropleth